In [ ]:


---


# P7 - Implémentez un modèle de scoring

---
La société financière  "Prêt à dépenser"propose des crédits à la consommation pour des personnes ayant peu ou pas du tout d'historique de prêt. 
L’entreprise souhaite mettre en œuvre un outil de “scoring crédit” pour calculer la probabilité qu’un client rembourse son crédit, puis classifie la demande en crédit accordé ou refusé.
**Missions**
- Construire un modèle de scoring qui donnera une prédiction sur la probabilité de faillite d'un client de façon automatique.
- Construire un dashboard interactif à destination des gestionnaires de la relation client permettant d'interpréter les prédictions faites par le modèle, et d’améliorer la connaissance client des chargés de relation client.
- Mettre en production le modèle de scoring de prédiction à l’aide d’une API, ainsi que le dashboard interactif qui appelle l’API pour les prédictions.


Dans le présent Notebook , je présente la partie datadrift avec evidently .

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from zipfile import ZipFile
from sklearn.metrics import classification_report, confusion_matrix, roc_curve
import numpy as np
import joblib
import seaborn as sns

In [2]:
z1 = ZipFile("derniercsv/X_sample.zip")
train = pd.read_csv(z1.open('X_sample.csv'),  index_col='SK_ID_CURR',encoding ='utf-8')


In [3]:
z2 = ZipFile("derniercsv/X_sample_test.zip")
test = pd.read_csv(z2.open('X_sample_test.csv'), index_col='SK_ID_CURR', encoding ='utf-8')

In [4]:
lgbm = joblib.load("derniercsv/lgbm.pkl")


In [5]:
train

NAME_CONTRACT_TYPE  CODE_GENDER  FLAG_OWN_CAR  CNT_CHILDREN  \
SK_ID_CURR                                                                
336286                     0.0          0.0           1.0      0.000000   
338986                     0.0          0.0           0.0      0.000000   
145942                     0.0          0.0           0.0      0.000000   
198106                     0.0          1.0           1.0      0.052632   
132865                     0.0          1.0           0.0      0.000000   
...                        ...          ...           ...           ...   
380250                     0.0          0.0           1.0      0.000000   
380059                     0.0          1.0           1.0      0.000000   
163082                     0.0          0.0           0.0      0.000000   
448502                     0.0          1.0           0.0      0.105263   
236961                     0.0          0.0           0.0      0.052632   

            AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
SK_ID_CURR                                                               
336286              0.000473    0.184000     0.116128         0.158249   
338986              0.000627    0.157303     0.070674         0.158249   
145942              0.000935    0.270787     0.122499         0.271605   
198106              0.003628    0.107056     0.202668         0.102132   
132865              0.001012    0.157303     0.078624         0.158249   
...                      ...         ...          ...              ...   
380250              0.000935    0.100638     0.056458         0.068462   
380059              0.001435    0.117298     0.196823         0.108866   
163082              0.001704    0.108239     0.175483         0.103255   
448502              0.000473    0.059775     0.045911         0.046016   
236961              0.001897    0.224719     0.101966         0.225589   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  ...  \
SK_ID_CURR                                          ...   
336286                        0.392880    0.034893  ...   
338986                        0.268617    0.900225  ...   
145942                        0.226010    0.259357  ...   
198106                        0.134537    0.502255  ...   
132865                        0.142153    0.468038  ...   
...                                ...         ...  ...   
380250                        0.491595    0.408906  ...   
380059                        0.134537    0.190192  ...   
163082                        0.097483    0.384047  ...   
448502                        0.254009    0.300056  ...   
236961                        0.079177    0.429594  ...   

            ORGANIZATION_TYPE_Military  ORGANIZATION_TYPE_Police  \
SK_ID_CURR                                                         
336286                             0.0                       0.0   
338986                             0.0                       0.0   
145942                             0.0                       0.0   
198106                             0.0                       0.0   
132865                             0.0                       0.0   
...                                ...                       ...   
380250                             0.0                       0.0   
380059                             0.0                       0.0   
163082                             0.0                       0.0   
448502                             0.0                       0.0   
236961                             0.0                       0.0   

            ORGANIZATION_TYPE_School  ORGANIZATION_TYPE_Security Ministries  \
SK_ID_CURR                                                                    
336286                           0.0                                    0.0   
338986                           0.0                                    0.0   
145942                           0.0                                    0.0   
198106                   

In [6]:
test

NAME_CONTRACT_TYPE  CODE_GENDER  FLAG_OWN_CAR  CNT_CHILDREN  \
SK_ID_CURR                                                                
354273                     0.0          0.0           0.0      0.000000   
197040                     0.0          1.0           0.0      0.000000   
295396                     0.0          1.0           0.0      0.000000   
237563                     0.0          1.0           1.0      0.157895   
259044                     0.0          1.0           1.0      0.000000   
...                        ...          ...           ...           ...   
216272                     0.0          0.0           0.0      0.000000   
329383                     0.0          0.0           0.0      0.000000   
420383                     0.0          0.0           0.0      0.000000   
428757                     0.0          0.0           0.0      0.000000   
113599                     0.0          1.0           1.0      0.052632   

            AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
SK_ID_CURR                                                               
354273              0.001127    0.186557     0.161285         0.147026   
197040              0.002474    0.029758     0.061443         0.026936   
295396              0.000742    0.025843     0.050614         0.026936   
237563              0.000935    0.101124     0.129519         0.102132   
259044              0.000935    0.078171     0.069954         0.053872   
...                      ...         ...          ...              ...   
216272              0.000935    0.252983     0.142436         0.217733   
329383              0.000473    0.044944     0.038505         0.046016   
420383              0.000935    0.022472     0.022253         0.023569   
428757              0.000127    0.056180     0.047964         0.057239   
113599              0.000550    0.027811     0.058249         0.023569   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  ...  \
SK_ID_CURR                                          ...   
354273                        0.024260   -1.208455  ...   
197040                        0.421848   -1.770237  ...   
295396                        0.248124   -1.757610  ...   
237563                        0.311695   -1.008794  ...   
259044                        0.245631   -1.058568  ...   
...                                ...         ...  ...   
216272                        0.635991   -1.602593  ...   
329383                        0.392880   -1.017362  ...   
420383                        0.254009   -1.650451  ...   
428757                        0.206749   -1.576099  ...   
113599                        0.254009   -1.075254  ...   

            ORGANIZATION_TYPE_Insurance  ORGANIZATION_TYPE_Military  \
SK_ID_CURR                                                            
354273                              0.0                         0.0   
197040                              0.0                         0.0   
295396                              0.0                         0.0   
237563                              0.0                         0.0   
259044                              0.0                         0.0   
...                                 ...                         ...   
216272                              0.0                         0.0   
329383                              0.0                         0.0   
420383                              0.0                         0.0   
428757                              0.0                         0.0   
113599                              0.0                         0.0   

            ORGANIZATION_TYPE_Police  ORGANIZATION_TYPE_School  \
SK_ID_CURR                                                       
354273                           0.0                       0.0   
197040                           0.0                       0.0   
295396                           0.0                       0.0   
237563                           0.0               

In [7]:
#je calcule le score de probabilité pour le test : si >
# Effectuer les prédictions sur les données de test
predictions_proba = lgbm.predict_proba(test)[:,1]

# Calculer la colonne TARGET en fonction de la probabilité prédite
threshold = 0.59
test['TARGET'] = 0
test.loc[predictions_proba >= threshold, 'TARGET'] = 1


In [8]:
test[test['TARGET']==1]

NAME_CONTRACT_TYPE  CODE_GENDER  FLAG_OWN_CAR  CNT_CHILDREN  \
SK_ID_CURR                                                                
354273                     0.0          0.0           0.0      0.000000   
295396                     0.0          1.0           0.0      0.000000   
259044                     0.0          1.0           1.0      0.000000   
338341                     0.0          1.0           1.0      0.000000   
110011                     0.0          0.0           0.0      0.000000   
...                        ...          ...           ...           ...   
454412                     0.0          0.0           1.0      0.000000   
417974                     0.0          0.0           0.0      0.000000   
334419                     0.0          1.0           1.0      0.000000   
444359                     0.0          1.0           0.0      0.000000   
113599                     0.0          1.0           1.0      0.052632   

            AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
SK_ID_CURR                                                               
354273              0.001127    0.186557     0.161285         0.147026   
295396              0.000742    0.025843     0.050614         0.026936   
259044              0.000935    0.078171     0.069954         0.053872   
338341              0.000742    0.050876     0.096069         0.046016   
110011              0.000550    0.090517     0.082432         0.079686   
...                      ...         ...          ...              ...   
454412              0.003243    0.137109     0.112513         0.107744   
417974              0.000742    0.056809     0.058722         0.046016   
334419              0.001127    0.058292     0.078238         0.046016   
444359              0.000473    0.078652     0.088031         0.079686   
113599              0.000550    0.027811     0.058249         0.023569   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  ...  \
SK_ID_CURR                                          ...   
354273                        0.024260   -1.208455  ...   
295396                        0.248124   -1.757610  ...   
259044                        0.245631   -1.058568  ...   
338341                        0.429796   -1.553157  ...   
110011                        0.197042   -1.761725  ...   
...                                ...         ...  ...   
454412                        0.344429   -1.374070  ...   
417974                        0.276330   -1.765614  ...   
334419                        0.196267   -1.264543  ...   
444359                        0.197042   -0.920857  ...   
113599                        0.254009   -1.075254  ...   

            ORGANIZATION_TYPE_Military  ORGANIZATION_TYPE_Police  \
SK_ID_CURR                                                         
354273                             0.0                       0.0   
295396                             0.0                       0.0   
259044                             0.0                       0.0   
338341                             0.0                       0.0   
110011                             0.0                       0.0   
...                                ...                       ...   
454412                             0.0                       0.0   
417974                             0.0                       0.0   
334419                             0.0                       0.0   
444359                             0.0                       0.0   
113599                             0.0                       0.0   

            ORGANIZATION_TYPE_School  ORGANIZATION_TYPE_Security Ministries  \
SK_ID_CURR                                                                    
354273                           0.0                                    0.0   
295396                           0.0                                    0.0   
259044                           0.0                                    0.0   
338341                   

In [9]:
test.reset_index(drop=True, inplace=True)
train.reset_index(drop=True, inplace=True)


In [10]:
from evidently import ColumnMapping
from evidently.report import Report
from evidently.metrics.base_metric import generate_column_metrics
from evidently.metric_preset import DataDriftPreset, TargetDriftPreset, DataQualityPreset, RegressionPreset
from evidently.test_suite import TestSuite
from evidently.tests.base_test import generate_column_tests
from evidently.test_preset import DataStabilityTestPreset, NoTargetPerformanceTestPreset, RegressionTestPreset


In [11]:
reference = train.copy()
current = test.copy()

In [12]:
report = Report(metrics=[
    DataDriftPreset(), 
])

report.run(reference_data=reference, current_data=current)
report

In [13]:
report.save_html("report_evidently_all.html")
